In [ ]:
import datetime
from pandas.tseries.offsets import BDay, MonthEnd
import globeop_reports as go
import pandas as pd
import analytics
import numpy as np

from analytics.index_data import get_index_quotes
from analytics.scenarios import run_portfolio_scenarios
from analytics import BlackSwaption, CreditIndex, BlackSwaptionVolSurface, Portfolio,DualCorrTranche
from copy import deepcopy

from risk.tranches import get_tranche_portfolio
from risk.swaptions import get_swaption_portfolio
from risk.bonds import subprime_risk, clo_risk, crt_risk

from utils.db import dbconn, dbengine, serenitas_engine, dawn_engine

In [ ]:
#PNL Allocation
date = datetime.date.today() - BDay(1)
report_date = date - MonthEnd(1)
report_date

In [ ]:
################################### Find the strategies that are not defined: undefined needs to be mapped in strat_map
strats = pd.read_csv('/home/serenitas/edwin/Python/strat_map.csv')
nav = go.get_net_navs()
m_pnl = go.get_monthly_pnl(['strat', 'custacctname'])
m_pnl = m_pnl.reset_index().merge(strats, on=['strat', 'custacctname'], how='left')
undefined = m_pnl[m_pnl.pnl.isna()].groupby(['strat', 'custacctname']).last()
#Get PNL Allocation
#Input latest NAVS to: '/home/serenitas/edwin/Python/subscription_fee_data.csv'
pnl_alloc = m_pnl.groupby(['date', 'pnl']).sum()
pnl_alloc = pnl_alloc.join(nav.begbooknav)
pnl_alloc['strat_return'] = pnl_alloc.mtdtotalbookpl / pnl_alloc.begbooknav
#rolling 12 months PNL per strategy - copy to RiskMonitor
start_date = report_date - pd.tseries.offsets.MonthEnd(11)
rolling_return = pnl_alloc[start_date:report_date].groupby('pnl').sum()['strat_return']
rolling_return.to_clipboard()

In [ ]:
rolling_return

In [ ]:
################################### Average Portfolio Sales Turnover - as of last monthend from today
#(total Bond Sales Proceeds + paydown)/average starting 12 months NAV
#Actually: Rolling 12 months sum of (total bond sales proceeds + paydown)/monthly NAV
nav = go.get_net_navs()
fund='SERCGMAST'
sql_string = "SELECT * FROM bonds WHERE buysell IS False and fund = %s"
df = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       params=[fund,],
                       index_col = 'trade_date')
df = df.groupby(pd.Grouper(freq='M')).sum()
#Average traded volume (Bonds only)

#Now get portfolio paydown per month
portfolio = go.get_portfolio()
portfolio = portfolio[(portfolio.custacctname == 'V0NSCLMAMB') &
                    (portfolio.identifier != 'USD') &
                    (portfolio.endqty != 0)]
cf = pd.read_sql_query("SELECT * FROM cashflow_history", dawn_engine,
                       parse_dates=['date'],
                       index_col=['date']).sort_index()
portfolio = portfolio.set_index('identifier', append=True)
portfolio = portfolio['endqty'].groupby(['identifier', 'periodenddate']).sum()
portfolio = portfolio.reset_index('identifier')
df_1 = pd.merge_asof(cf, portfolio.sort_index(), left_index=True, right_index=True, by='identifier')
df_1 = df_1.dropna(subset=['endqty'])
df_1 = df_1[(df_1.principal_bal != 0) & (df_1.principal != 0)]
df_1['paydown'] = df_1.apply(lambda df: df.endqty/df.principal_bal * df.principal, axis=1)
paydowns = df_1.paydown.groupby(pd.Grouper(freq='M')).sum()
temp = pd.concat([paydowns, df.principal_payment, df.accrued_payment], axis=1).fillna(0)
turnover = (temp.sum(axis=1)/nav.begbooknav).rolling(12).sum()
turnover[12:].plot()
turnover.min(), turnover.max(), turnover.mean()
turnover[-1]

In [ ]:
################################### BRINKER: Average Portfolio Sales Turnover - as of last monthend from today
#(total Bond Sales Proceeds + paydown)/average starting 12 months NAV
#Actually: Rolling 12 months sum of (total bond sales proceeds + paydown)/monthly NAV
nav = go.get_net_navs()
fund='BRINKER'
sql_string = "SELECT * FROM bonds WHERE buysell IS False and fund = %s"
df = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       params=[fund,],
                       index_col = 'trade_date')
df = df.groupby(pd.Grouper(freq='M')).sum()

cf = pd.read_sql_query("SELECT * FROM cashflow_history", dawn_engine,
                       parse_dates=['date'],
                       index_col=['date']).sort_index()
sql_string = "SELECT description, identifier, notional, price, factor FROM risk_positions(%s, %s, 'BRINKER')"
pos = {}
for d in cf.index.unique():
    for ac in ['Subprime', 'CRT']:
        pos[d, ac] = pd.read_sql_query(sql_string, dawn_engine, params=[d.date(), ac])
pos = pd.concat(pos, names=['date', 'asset_class'])
pos = pos.reset_index(level=[1,2])

In [ ]:
################################### Number of position (min/max/average) /position size (min/max/average) /Top 10 position size
portfolio = go.get_portfolio()
nav = go.get_net_navs()
exc_port_list = [None, 'SERCGLLC__SERCGLLC', 'CASH', 'SERCGLTD__SERCGLTD', 'GFS_HELPER_BUSINESS_UNIT', 'SER_TEST__SER_TEST']
exc_inst_list = ['CAD', 'CADF', 'SEREONUS', 'USD', 'USDF', 'USDLOAN', 'EUR', 'EURLOAN', 'USDCASHINT',
                 'USDLOANOLD', 'USDSWAPFEE', 'EURF','CADCASHINT','COMMISSIONFEES', 'EURCASHINT', 'COMMUNICATIONFEES']
exc_inst_list2 = ['86359DUR6OLD2','004375DV0OLD4','32027GAD8OLD7','75406DAC7OLD7','86359DMN4OLD7','45661EAW4OLD7']

portfolio = portfolio[~portfolio.port.isin(exc_port_list) &
                      ~portfolio.identifier.isin(exc_inst_list) &
                      ~portfolio.identifier.isin(exc_inst_list2)]

all_positions = portfolio.groupby(['periodenddate', 'identifier'])['endbooknav'].sum() 
num_pos = all_positions.groupby('periodenddate').count()
#min/max/mean number of positions
num_pos.min(), num_pos.max(), num_pos.mean()

bonds = portfolio[(portfolio.custacctname == 'V0NSCLMAMB') &
                    (portfolio.identifier != 'USD') &
                    (portfolio.endqty != 0) &
                    (portfolio.port.isin(['MORTGAGES', 'STRUCTURED', 'CLO'])) &
                    (~portfolio.strat.isin(['MBSCDS']))]

monthend_bonds = bonds.groupby(pd.Grouper(freq="M"), group_keys=False).apply(
        lambda df: df.loc[df.index[-1]]
    )
monthend_bonds = monthend_bonds.groupby(['periodenddate', 'identifier']).sum()
nav.index.rename('periodenddate', inplace=True)
monthend_bonds = monthend_bonds.merge(nav, left_index=True, right_index=True, suffixes=('_bond', '_fund'))
monthend_bonds['percentage'] = monthend_bonds.endbooknav_bond/monthend_bonds.endbooknav_fund
last_date = monthend_bonds.index.get_level_values(0).max() 
latest = monthend_bonds.loc[last_date]
#min/max/mean position size
latest['percentage'][latest['percentage']>0.0000001].min(), latest['percentage'].max(), latest['percentage'].mean()
#10th largest positions
ten_largest = monthend_bonds.groupby('periodenddate').apply(lambda df: df['percentage'].nlargest(10).sum())
ten_largest.min(), ten_largest.max(), ten_largest.mean()

In [ ]:
################################### Average Traded Volume
nav = go.get_net_navs()
sql_string = "SELECT * FROM bonds where fund='SERCGMAST'"
bond_trades = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       index_col = 'trade_date')
g = bond_trades['principal_payment'].groupby(pd.Grouper(freq='M'))
#min/max/mean bond trades by count (weekly = /4)
g.count().min()/4, g.count().max()/4, g.count().mean()/4
#min/max/mean bond trades by MV (weekly = /4)
volume = g.sum()/nav.endbooknav
volume.min()/4, volume.max()/4, volume.mean()/4

sql_string = "SELECT * FROM cds where fund='SERCGMAST'"
cds_trades = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       index_col = 'trade_date')
g = cds_trades['notional'].groupby(pd.Grouper(freq='M'))
#min/max/mean cds trades by count
g.count().min()/4, g.count().max()/4, g.count().mean()/4
#min/max/mean cds trades by notional
volume = g.sum()/nav.endbooknav
volume.fillna(0, inplace=True)
volume.min(), volume.max()/4, volume.mean()/4

#Max trades per day - CDS trades only, bond trades only, combined bond/cds trades
cds_trades[cds_trades.cp_code != 'CONTRA'].groupby(pd.Grouper(freq='D')).count().max()
bond_trades.groupby(pd.Grouper(freq='D')).count().max()
cds_trades[cds_trades.cp_code != 'CONTRA'].id.append(bond_trades.id).groupby(pd.Grouper(freq='D')).count().max()

In [ ]:
################################### Average Holding Period
#Time series of bond portfolio age (portfolio date - latest buy date of position) - weighted by MV of all bonds.
#Problem is if we buy the same position again it resets to the holding period to 0
nav = go.get_net_navs()
sql_string = "SELECT * FROM bonds where fund = 'SERCGMAST' order by trade_date desc"
df = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       index_col = 'trade_date')
buys = df[df.buysell == True].sort_index()
buys['buy_date'] = buys.index
#get portfolio 
port = go.get_portfolio()
port.sort_index(inplace=True)
buy_dates = pd.merge_asof(port, buys[['buy_date', 'identifier']], left_index=True, right_index=True,by='identifier', direction='backward')
buy_dates = buy_dates[['identifier', 'endbooknav','buy_date']][~buy_dates.buy_date.isna()]
buy_dates['hold_days'] = (buy_dates.index - buy_dates.buy_date)/np.timedelta64(1, 'D')
def weighted_average(df):
    return np.average(df.hold_days,weights=df.endbooknav)
hold_period = buy_dates.groupby('periodenddate').apply(func = weighted_average)
hold_period_last_five = hold_period.loc[datetime.date.today()- datetime.timedelta(weeks=52*5)::]
hold_period_last_five.min(), hold_period_last_five.max(), hold_period_last_five.mean()

In [ ]:
################################## Calculate Historical Bond Duration/Yield
analytics.init_ontr()
mysql_engine = dbengine('rmbs_model')
dates = pd.date_range(datetime.date(2013, 1, 30), pd.datetime.today() - MonthEnd(1), freq="M")
calc_df = pd.DataFrame()
sql_string = ("SELECT distinct timestamp::date FROM priced where normalization = 'current_notional' and model_version = 1 "
              "and date(timestamp) < %s and date(timestamp) > %s order by timestamp desc")
with dbconn('etdb') as etconn, dbconn('dawndb') as dawnconn:
    for d in dates:
        timestamps = pd.read_sql_query(sql_string, dawn_engine, parse_dates=["timestamp"], params=[d, d - pd.tseries.offsets.DateOffset(15, "D")])
        calc_df = calc_df.append(subprime_risk(d.date(), dawnconn, mysql_engine, timestamps.iloc[0,0].date()))
calc_df=calc_df.reset_index().set_index('date')
calc_df = calc_df.dropna(subset=['bond_yield', 'hy_equiv']) 
bond_stats = pd.DataFrame()
for d, g in calc_df.groupby(pd.Grouper(freq='M')):
        bond_stats.loc[d, 'dur'] = sum(g.notional * g.factor * g.modDur)/sum(g.notional * g.factor)
        bond_stats.loc[d, 'yield'] = sum(g.usd_market_value * g.modDur * g.bond_yield) /sum(g.usd_market_value * g.modDur)

In [ ]:
################################## Leverage Ratio
nav = go.get_net_navs()
portfolio = go.get_portfolio()
monthend_portfolio = portfolio.groupby(pd.Grouper(freq="M"), group_keys=False).apply(
        lambda df: df.loc[df.index[-1]]
    )
monthend_byinvid = monthend_portfolio.groupby(['periodenddate','invid']).sum()
positive = monthend_byinvid['endbooknav'].groupby(['periodenddate']).agg(lambda x: x[x>0].sum())
nav = nav.merge(positive, left_index=True, right_index=True)
nav['leverage'] = nav.endbooknav_y/nav.endbooknav_x
nav['leverage'].plot()

In [ ]:
################################## FX Exposure, any net CAD/EUR exposures are FX exposure. 
################### doesn't add up to 1 including the USD as we now sum up all the NAVs after adjusting the Futures
nav = go.get_net_navs()
portfolio = go.get_portfolio()
monthend_portfolio = portfolio.groupby(pd.Grouper(freq="M"), group_keys=False).apply(
        lambda df: df.loc[df.index[-1]]
    )
#Adjust the endbooknav of futures
tickers = ['CD_CME', 'EC_CME']
factors = [100000, 125000]
currency = ['CAD', 'EUR']
for a, b, c  in zip(tickers, factors, currency):
    new_endbooknav = monthend_portfolio['endqty'] * monthend_portfolio['endlocalmarketprice'] * b
    monthend_portfolio['endbooknav'] = new_endbooknav.where(monthend_portfolio['invid'].str.contains(a), monthend_portfolio['endbooknav'])
    monthend_portfolio.loc[monthend_portfolio['invid'].str.contains(a), 'invccy'] = c

monthend_portfolio = monthend_portfolio.merge(nav, left_index=True, right_index=True, suffixes=('_inst', '_fund'))
monthend_portfolio.index.name = 'periodenddate'
monthend_portfolio['percent_nav'] = monthend_portfolio['endbooknav_inst']/monthend_portfolio['endbooknav_fund']

collateral_filter =monthend_portfolio['invid'].str.contains('LOAN')
futures_filter = monthend_portfolio['invid'].str.contains('|'.join(tickers))
cash_filter = ((monthend_portfolio['invid'] == 'CAD') | (monthend_portfolio['invid'] == 'EUR'))
trades = monthend_portfolio[(~futures_filter) & (~collateral_filter) & (~cash_filter)]
names = ['collateral', 'futures', 'cash', 'trades']
categories = [monthend_portfolio[collateral_filter], 
              monthend_portfolio[futures_filter], 
              monthend_portfolio[cash_filter],
              trades]
exposure = {}
for n, x in zip(names, categories):
    exposure[n] = x.groupby(['periodenddate', 'invccy']).sum()
exposure = pd.concat(exposure)['percent_nav']
exposure.unstack(level=1).T.to_clipboard()

In [ ]:
################################## Historical Notioinals and HY Equiv
dates = pd.date_range(datetime.date(2013, 1, 30), pd.datetime.today() - MonthEnd(1), freq="BM")
#look for a day with HY quotes... we need that to construct HY Equiv
sql_string = 'select distinct(date) from index_quotes where index = %s order by date asc'
hy_dates = pd.read_sql_query(sql_string, serenitas_engine, parse_dates = 'date', params=['HY',])
def nearest(items, pivot):
    return min(items, key=lambda x: abs(x - pivot))
hy_dates.apply(lambda x: nearest(dates, x))
pd.merge_asof(pd.DataFrame(dates), hy_dates, left_index=True, right_index=True)
portfs = {}
for d in dates:
    d = d.date()
    portfs[d] = build_portf(d)

In [ ]:
#### Function to build portfolio
def build_portf(position_date, spread_date=None):
    analytics.init_ontr()
    if spread_date is None:
        spread_date=position_date
    conn = dawn_engine.raw_connection()
    mysql_engine = dbengine('rmbs_model')
    mysqlcrt_engine = dbengine('crt')
    
    on_the_run_index = CreditIndex('HY', on_the_run('HY', position_date), '5yr', value_date=position_date)

    #tranche positions
    portf = get_tranche_portfolio(position_date, conn, False, 'SERCGMAST')
    #swaption positions
    s_portf = get_swaption_portfolio(position_date, conn)
    if bool(s_portf):
        for t, id in zip(s_portf.trades, s_portf.trade_ids):
            portf.add_trade(t, id)

    #index positions
    df = pd.read_sql_query("SELECT * from list_cds_positions_by_strat(%s)",
                            dawn_engine, params=(position_date,))
    if not(df.empty):
        df_no_curve = df[~df.folder.str.contains("CURVE")]
        for t in df_no_curve.itertuples(index=False):
            portf.add_trade(CreditIndex(redcode=t.security_id, maturity=t.maturity, notional=t.notional),
                           (t.folder, t.security_desc))

        #separately add in curve delta
        df_curve = df[df.folder.str.contains("CURVE")]
        curve_portf = Portfolio([CreditIndex(redcode=t.security_id, maturity=t.maturity, notional=t.notional)
                                 for t in df_curve.itertuples(index=False)])
        curve_portf.value_date = spread_date
        curve_portf.mark()

        hyontr = deepcopy(on_the_run_index)
        hyontr.notional = curve_portf.hy_equiv
        portf.add_trade(hyontr, ('curve_trades', ''))

    #get bond risks:
    sql_string = ("SELECT distinct timestamp::date FROM priced where normalization = 'current_notional' and model_version = 1 "
              "and date(timestamp) <= %s and date(timestamp) >= %s order by timestamp desc")
    with dbconn('etdb') as etconn, dbconn('dawndb') as dawnconn:
        timestamps = pd.read_sql_query(sql_string, dawn_engine, parse_dates=["timestamp"], 
                                       params=[position_date, position_date - pd.tseries.offsets.DateOffset(15, "D")])
        rmbs_pos = subprime_risk(position_date, dawnconn, mysql_engine, timestamps.iloc[0][0].date())
        clo_pos = clo_risk(position_date, dawnconn, etconn)
        crt_pos = crt_risk(position_date, dawnconn, mysqlcrt_engine, model_version = 'hpi5_ir3_btm')
    rmbs_notional = 0
    for pos in [rmbs_pos, crt_pos]:
        rmbs_notional += pos['hy_equiv'].sum() if pos is not None else 0
    hyontr_rmbs = deepcopy(on_the_run_index)
    hyontr_rmbs.notional = -rmbs_notional
    portf.add_trade(hyontr_rmbs, ('rmbs_bonds', ''))
    if isinstance(clo_pos, pd.DataFrame):
        hyontr_clos = deepcopy(on_the_run_index)
        hyontr_clos.notional = -clo_pos['hy_equiv'].sum()
        portf.add_trade(hyontr_clos, ('clo_bonds', ''))
    
    portf.value_date = spread_date
    portf.mark(interp_method="bivariate_linear")
    portf.reset_pv()
    
    return portf

In [ ]:
################################### Calculate stress scenario 
position_date = (datetime.date.today() - BDay(1)).date()
spread_date = position_date
analytics.init_ontr(spread_date)

In [ ]:
#Calculate amount of stress for reports
from analytics.curve_trades import on_the_run
df = get_index_quotes('HY', list(range(on_the_run('HY', spread_date) - 10, on_the_run('HY', spread_date) + 1)),
                          tenor=['5yr'], years=5)
df = df.xs('5yr', level='tenor')['close_spread'].groupby(['date', 'series']).last()
df=df.loc[:'2020-2-28']

widen, tighten = [], []
#approximately 1,3,6 months move (22 each months)
for days in [22, 66, 132]: 
    calc = df.unstack().pct_change(freq= str(days)+'B').stack().groupby('date').last()
    widen.append(calc.max())
    tighten.append(calc.min())
pd.DataFrame([widen, tighten], columns=['1M', '3M', '6M'], index=['widen', 'tighten'])

In [ ]:
#tranche/swaption positions
portf = build_portf(position_date, spread_date)

vol_surface = {}
for trade in portf.swaptions:
    try:
        vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                                     value_date=spread_date, interp_method = "bivariate_linear")
    except:
        vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series + 1, 
                                     value_date=spread_date, interp_method = "bivariate_linear")
    vol_surface[(trade.index.index_type, trade.index.series, trade.option_type)] = vs[vs.list(source='MS', option_type=trade.option_type)[-1]]

scens = run_portfolio_scenarios(portf, date_range=[pd.Timestamp(spread_date)], params=["pnl"],
                                spread_shock=widen,
                                vol_shock=[0],
                                corr_shock = [0],
                                vol_surface=vol_surface)

attrib = (scens.
          reset_index(level=['date'], drop=True).
          groupby(level=0, axis=1).sum())
results = attrib.xs((widen[2], 0., 0.), level=['spread_shock', 'corr_shock', 'vol_shock']).T

In [ ]:
results

In [ ]:
results.to_csv('/home/serenitas/edwin/Python/reto_results.csv')

In [ ]:
################################### Run set of scenario
spread_shock = np.round(np.arange(-.2, 1, .05), 3)
scens = run_portfolio_scenarios(portf, date_range=[pd.Timestamp(spread_date)], params=['pnl', 'delta'],
                                spread_shock=spread_shock,
                                vol_shock=[.5],
                                corr_shock=[0],
                                vol_surface=vol_surface)

pnl = scens.xs('pnl', axis=1, level=2)
pnl = pnl.xs((0,0), level=['vol_shock', 'corr_shock'])

scenarios = (pnl.
          reset_index(level=['date'], drop=True).
          groupby(level=0, axis=1).sum())

options = ['HYOPTDEL', 'HYPAYER', 'HYREC', 'IGOPTDEL', 'IGPAYER', 'IGREC']
tranches = ['HYMEZ', 'HYINX', 'HYEQY', 'IGMEZ', 'IGINX', 'IGEQY', 'IGSNR', 'IGINX', 'BSPK', 'XOMEZ', 'XOINX']

scenarios['options'] = scenarios[set(scenarios.columns).intersection(options)].sum(axis=1)
scenarios['tranches'] = scenarios[set(scenarios.columns).intersection(tranches)].sum(axis=1)

synthetic = scenarios[['options', 'tranches', 'curve_trades']]
synthetic['total'] = synthetic.sum(axis = 1)
nav = go.get_net_navs()
(synthetic/nav.endbooknav[-1]).plot()